In [13]:
# Data manipulation
# ==============================================================================
import numpy as np
import pandas as pd

# Plots
# ==============================================================================
import matplotlib.pyplot as plt
plt.style.use('fivethirtyeight')
plt.rcParams['lines.linewidth'] = 1.5
%matplotlib inline

# Modeling and Forecasting
# ==============================================================================
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import Lasso
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import make_pipeline

from skforecast.ForecasterAutoreg import ForecasterAutoreg
from skforecast.ForecasterAutoregCustom import ForecasterAutoregCustom
from skforecast.ForecasterAutoregDirect import ForecasterAutoregDirect
from skforecast.model_selection import grid_search_forecaster
from skforecast.model_selection import random_search_forecaster
from skforecast.model_selection import backtesting_forecaster
from skforecast.model_selection import bayesian_search_forecaster
from skforecast.utils import save_forecaster
from skforecast.utils import load_forecaster

from xgboost import XGBRegressor
from lightgbm import LGBMRegressor
from catboost import CatBoostRegressor

# Warnings configuration
# ==============================================================================
import warnings
# warnings.filterwarnings('ignore')


In [14]:
dx = pd.read_csv(r'/home/nkem/Documents/PhD_Research/dlam.csv')
dx['incidentdate'] = pd.to_datetime(dx['incidentdate'])
#data = dx.drop(columns="estimatedqty", axis= 1, inplace=True)
data = dx.copy()

data['incidentdate'] = pd.to_datetime(data['incidentdate'], format='%Y/%m/%d')
#data = data.asfreq('MS')
data = data.set_index("incidentdate")
data = data.sort_index()

# split the data into a train dataframe and X_test and y_test dataframes, where the number of samples for test is equal to
# the number of periods the user wants to predict
end_train = '2021-01-31'
end_validation = '2021-06-30'

In [15]:
data

estimatedqty  spillno  year      month
incidentdate                                        
2005-01-31       100.05700        3  2005    January
2005-02-28         0.03000        1  2005   February
2005-03-31         3.06000        2  2005      March
2005-04-30       820.30040       32  2005      April
2005-05-31        59.00000        2  2005        May
...                    ...      ...   ...        ...
2021-08-31       205.20000       14  2021     August
2021-09-30     13177.78000       21  2021  September
2021-10-31      3888.33140       15  2021    October
2021-11-30       129.51400       17  2021   November
2021-12-31      1262.54904       27  2021   December

[204 rows x 4 columns]

In [16]:
# Store categorical variables as category type
# ==============================================================================
#data['estimatedqty'] = data['estimatedty'].astype('category')
data['month']   = data['month'].astype('category')
data['year'] = data['year'].astype('category')
#data['year'] = data['year'].astype('category')
#data['day'] = data['day'].astype('category')

In [17]:
data

estimatedqty  spillno  year      month
incidentdate                                        
2005-01-31       100.05700        3  2005    January
2005-02-28         0.03000        1  2005   February
2005-03-31         3.06000        2  2005      March
2005-04-30       820.30040       32  2005      April
2005-05-31        59.00000        2  2005        May
...                    ...      ...   ...        ...
2021-08-31       205.20000       14  2021     August
2021-09-30     13177.78000       21  2021  September
2021-10-31      3888.33140       15  2021    October
2021-11-30       129.51400       17  2021   November
2021-12-31      1262.54904       27  2021   December

[204 rows x 4 columns]

In [18]:
 #One hot encoding
# ==============================================================================
data = pd.get_dummies(data, columns=['year', 'month'])
data.head(3)

# Select exogenous variables, including those generated by one hot encoding.
exog_variables = [column for column in data.columns
                      if column.startswith(('year', 'month'))]
#exog_variables.extend(['estimatedqty'])
print(exog_variables)

['year_2005', 'year_2006', 'year_2007', 'year_2008', 'year_2009', 'year_2010', 'year_2011', 'year_2012', 'year_2013', 'year_2014', 'year_2015', 'year_2016', 'year_2017', 'year_2018', 'year_2019', 'year_2020', 'year_2021', 'month_April', 'month_August', 'month_December', 'month_February', 'month_January', 'month_July', 'month_June', 'month_March', 'month_May', 'month_November', 'month_October', 'month_September']


In [7]:
# Bayesian search hyperparameter and lags with Optuna
# ==============================================================================
forecaster = ForecasterAutoreg(
                 regressor = CatBoostRegressor(random_state=123, silent=True),
                 lags      = 10 # Placeholder, the value will be overwritten
             )

# Lags used as predictors
lags_grid = range(1, 6)

# Regressor hyperparameters search space
def search_space(trial):
    search_space  = {'n_estimators'     : trial.suggest_int('n_estimators', 900, 920, step=1),
                     'min_samples_leaf' : trial.suggest_float('min_samples_leaf', 1., 3.7, log=True),
                     'max_features'     : trial.suggest_categorical('max_features', ['log2', 'sqrt']),
                     'max_depth'         : trial.suggest_int("max_depth", 1, 6, step=1),
                     #'learning rate'    : trial.suggest_float('learning_rate', 0.01, 0.3, step=0.01),
                     #'learning rate'    : trial.suggest_float('learning_rate', 0.01, 1),
                    "learning_rate"      : trial.suggest_loguniform("learning_rate", 1e-2, 1e0),
                    "loss_function"      : trial.suggest_categorical("loss_function", ["RMSE", "MAE"]),
                    #"l2_leaf_reg"        : trial.suggest_loguniform("l2_leaf_reg", 1e-2, 1e0),
                    #"colsample_bylevel": trial.suggest_float("colsample_bylevel", 0.01, 0.1),
                    "boosting_type": trial.suggest_categorical("boosting_type", ["Ordered", "Plain"]),
                    "bootstrap_type": trial.suggest_categorical("bootstrap_type", ["Bayesian", "Bernoulli", "MVS"]),
                    "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 2, 20),
                     "one_hot_max_size": trial.suggest_int("one_hot_max_size", 2, 20),

                     }
    return search_space

results, frozen_trial = bayesian_search_forecaster(
                            forecaster            = forecaster,
                            #y                     = data.loc[:end_val, 'y'],
                            y                     = data.loc[:end_validation, 'spillno'],
                           exog                   = data.loc[:end_validation, exog_variables],
                            lags_grid             = lags_grid,
                            search_space          = search_space,
                            steps                 = 12,
                            metric                = 'mean_absolute_error',
                            refit                 = True,
                            initial_train_size    = len(data.loc[:end_train]),
                            fixed_train_size      = True,
                            n_trials              = 100,
                            random_state          = 123,
                            return_best           = False,
                            verbose               = False,
                            engine                = 'optuna',
                            kwargs_create_study   = {},
                            kwargs_study_optimize = {}
                        )

results

Number of models compared: 500,
         100 bayesian search in each lag configuration.


loop lags_grid:   0%|                                               | 0/5 [00:00<?, ?it/s]/home/nkem/.local/lib/python3.10/site-packages/skforecast/utils/utils.py:360: UserWarning: `y` has DatetimeIndex index but no frequency. Index is overwritten with a RangeIndex of step 1.
  warnings.warn(
/home/nkem/.local/lib/python3.10/site-packages/skforecast/utils/utils.py:474: UserWarning: `exog` has DatetimeIndex index but no frequency. Index is overwritten with a RangeIndex of step 1.
  warnings.warn(
/home/nkem/.local/lib/python3.10/site-packages/skforecast/utils/utils.py:360: UserWarning: `y` has DatetimeIndex index but no frequency. Index is overwritten with a RangeIndex of step 1.
  warnings.warn(
/home/nkem/.local/lib/python3.10/site-packages/skforecast/utils/utils.py:474: UserWarning: `exog` has DatetimeIndex index but no frequency. Index is overwritten with a RangeIndex of step 1.
  warnings.warn(
/home/nkem/.local/lib/python3.10/site-packages/skforecast/utils/utils.py:417: UserWarnin

lags                                             params  \
152           [1, 2]  {'n_estimators': 909, 'max_depth': 4, 'learnin...   
169           [1, 2]  {'n_estimators': 910, 'max_depth': 3, 'learnin...   
147           [1, 2]  {'n_estimators': 909, 'max_depth': 3, 'learnin...   
148           [1, 2]  {'n_estimators': 909, 'max_depth': 3, 'learnin...   
133           [1, 2]  {'n_estimators': 909, 'max_depth': 6, 'learnin...   
..               ...                                                ...   
449  [1, 2, 3, 4, 5]  {'n_estimators': 915, 'max_depth': 3, 'learnin...   
459  [1, 2, 3, 4, 5]  {'n_estimators': 913, 'max_depth': 5, 'learnin...   
299        [1, 2, 3]  {'n_estimators': 914, 'max_depth': 5, 'learnin...   
465  [1, 2, 3, 4, 5]  {'n_estimators': 920, 'max_depth': 5, 'learnin...   
220        [1, 2, 3]  {'n_estimators': 902, 'max_depth': 6, 'learnin...   

     mean_absolute_error  n_estimators  max_depth  learning_rate  \
152             1.071095           909          4       0.188515   
169             1.595666           910          3       0.195529   
147             2.250194           909          3       0.341179   
148             2.270991           909          3       0.340668   
133             2.275504           909          6       0.133599   
..                   ...           ...        ...            ...   
449            24.080683           915          3       0.806863   
459            24.735069           913          5       0.771019   
299            26.313297           914          5       0.202863   
465            30.582331           920          5       0.495340   
220            30.634962           902          6       0.303205   

    loss_function boosting_type bootstrap_type  min_data_in_leaf  \
152           MAE       Ordered            MVS                17   
169           MAE       Ordered            MVS                14   
147           MAE       Ordered            MVS                14   
148           MAE       Ordered            MVS                15   
133           MAE         Plain       Bayesian                 7   
..            ...           ...            ...               ...   
449           MAE         Plain            MVS                11   
459           MAE         Plain      Bernoulli                20   
299           MAE       Ordered      Bernoulli                 3   
465           MAE         Plain       Bayesian                16   
220           MAE       Ordered      Bernoulli                 4   

     one_hot_max_size  
152                 8  
169                 8  
147                 8  
148                 9  
133                 3  
..                ...  
449                 9  
459                13  
299                10  
465                18  
220                 9  

[500 rows x 11 columns]

In [8]:
results.to_csv(r"/home/nkem/Documents/PhD_Research/results_catboost_bayesian.csv")

In [20]:
# Bayesian search hyperparameter and lags with Optuna
# ==============================================================================
forecaster = ForecasterAutoreg(
                 regressor = CatBoostRegressor(random_state=123, silent=True),
                 lags      = 10 # Placeholder, the value will be overwritten
             )

# Lags used as predictors
lags_grid = range(1, 6)

# Regressor hyperparameters search space
def search_space(trial):
    search_space  = {'n_estimators'     : trial.suggest_int('n_estimators', 900, 920, step=1),
                     #'min_samples_leaf' : trial.suggest_float('min_samples_leaf', 1., 3.7, log=True),
                     #'max_features'     : trial.suggest_categorical('max_features', ['log2', 'sqrt']),
                     'max_depth'         : trial.suggest_int("max_depth", 1, 6, step=1),
                     #'learning rate'    : trial.suggest_float('learning_rate', 0.01, 0.3, step=0.01),
                     #'learning rate'    : trial.suggest_float('learning_rate', 0.01, 1),
                    "learning_rate"      : trial.suggest_loguniform("learning_rate", 1e-2, 1e0),
                    "loss_function"      : trial.suggest_categorical("loss_function", ["RMSE", "MAE"]),
                    #"l2_leaf_reg"        : trial.suggest_loguniform("l2_leaf_reg", 1e-2, 1e0),
                    #"colsample_bylevel": trial.suggest_float("colsample_bylevel", 0.01, 0.1),
                    "boosting_type": trial.suggest_categorical("boosting_type", ["Ordered", "Plain"]),
                    "bootstrap_type": trial.suggest_categorical("bootstrap_type", ["Bayesian", "Bernoulli", "MVS"]),
                    "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 2, 20),
                     "one_hot_max_size": trial.suggest_int("one_hot_max_size", 2, 20),

                     }
    return search_space

results, frozen_trial = bayesian_search_forecaster(
                            forecaster            = forecaster,
                            #y                     = data.loc[:end_val, 'y'],
                            y                     = data.loc[:end_validation, 'spillno'],
                           exog                   = data.loc[:end_validation, exog_variables],
                            lags_grid             = lags_grid,
                            search_space          = search_space,
                            steps                 = 12,
                            metric                = 'mean_absolute_error',
                            refit                 = True,
                            initial_train_size    = len(data.loc[:end_train]),
                            fixed_train_size      = True,
                            n_trials              = 1000,
                            random_state          = 123,
                            return_best           = False,
                            verbose               = False,
                            engine                = 'optuna',
                            kwargs_create_study   = {},
                            kwargs_study_optimize = {}
                        )

results

Number of models compared: 5000,
         1000 bayesian search in each lag configuration.


loop lags_grid:   0%|                                               | 0/5 [00:00<?, ?it/s]/home/nkem/.local/lib/python3.10/site-packages/skforecast/utils/utils.py:360: UserWarning: `y` has DatetimeIndex index but no frequency. Index is overwritten with a RangeIndex of step 1.
  warnings.warn(
/home/nkem/.local/lib/python3.10/site-packages/skforecast/utils/utils.py:474: UserWarning: `exog` has DatetimeIndex index but no frequency. Index is overwritten with a RangeIndex of step 1.
  warnings.warn(
/home/nkem/.local/lib/python3.10/site-packages/skforecast/utils/utils.py:360: UserWarning: `y` has DatetimeIndex index but no frequency. Index is overwritten with a RangeIndex of step 1.
  warnings.warn(
/home/nkem/.local/lib/python3.10/site-packages/skforecast/utils/utils.py:474: UserWarning: `exog` has DatetimeIndex index but no frequency. Index is overwritten with a RangeIndex of step 1.
  warnings.warn(
/home/nkem/.local/lib/python3.10/site-packages/skforecast/utils/utils.py:417: UserWarnin

lags                                             params  \
1404           [1, 2]  {'n_estimators': 900, 'max_depth': 4, 'learnin...   
1626           [1, 2]  {'n_estimators': 919, 'max_depth': 4, 'learnin...   
1870           [1, 2]  {'n_estimators': 907, 'max_depth': 4, 'learnin...   
1180           [1, 2]  {'n_estimators': 907, 'max_depth': 4, 'learnin...   
1052           [1, 2]  {'n_estimators': 909, 'max_depth': 4, 'learnin...   
...               ...                                                ...   
3301     [1, 2, 3, 4]  {'n_estimators': 903, 'max_depth': 4, 'learnin...   
3587     [1, 2, 3, 4]  {'n_estimators': 902, 'max_depth': 4, 'learnin...   
4391  [1, 2, 3, 4, 5]  {'n_estimators': 904, 'max_depth': 5, 'learnin...   
3914     [1, 2, 3, 4]  {'n_estimators': 904, 'max_depth': 4, 'learnin...   
3999     [1, 2, 3, 4]  {'n_estimators': 901, 'max_depth': 4, 'learnin...   

      mean_absolute_error  n_estimators  max_depth  learning_rate  \
1404             0.788872           900          4       0.321465   
1626             0.805865           919          4       0.132784   
1870             0.887790           907          4       0.154233   
1180             1.020744           907          4       0.132821   
1052             1.071095           909          4       0.188515   
...                   ...           ...        ...            ...   
3301            37.643683           903          4       0.366103   
3587            38.575610           902          4       0.398444   
4391            41.512011           904          5       0.456504   
3914            43.744417           904          4       0.972210   
3999            44.206623           901          4       0.440548   

     loss_function boosting_type bootstrap_type  min_data_in_leaf  \
1404           MAE       Ordered            MVS                 9   
1626           MAE       Ordered            MVS                10   
1870           MAE       Ordered            MVS                10   
1180           MAE       Ordered            MVS                 8   
1052           MAE       Ordered            MVS                17   
...            ...           ...            ...               ...   
3301           MAE       Ordered       Bayesian                19   
3587           MAE       Ordered       Bayesian                 5   
4391           MAE         Plain       Bayesian                 5   
3914           MAE       Ordered       Bayesian                10   
3999           MAE       Ordered            MVS                 6   

      one_hot_max_size  
1404                10  
1626                12  
1870                 7  
1180                13  
1052                 8  
...                ...  
3301                14  
3587                15  
4391                16  
3914                12  
3999                12  

[5000 rows x 11 columns]